In [1]:
pip install pandas plotly networkx

Defaulting to user installation because normal site-packages is not writeable
     |████████████████████████████████| 9.6 MB 3.8 MB/s eta 0:00:01
     |████████████████████████████████| 1.6 MB 19.2 MB/s eta 0:00:01
     |████████████████████████████████| 385 kB 18.4 MB/s eta 0:00:01
You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


In [8]:
pip install matplotlib holoviews hvplot seaborn scipy openpyxl


Defaulting to user installation because normal site-packages is not writeable
     |████████████████████████████████| 250 kB 4.2 MB/s eta 0:00:01
You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


In [10]:
import pandas as pd
import numpy as np
from itertools import combinations
import matplotlib.pyplot as plt
import seaborn as sns
from scipy.stats import chi2_contingency
import networkx as nx
from collections import Counter
from matplotlib.colors import LinearSegmentedColormap
import matplotlib.patches as mpatches
from matplotlib.patches import Circle, Wedge, Polygon
from matplotlib.collections import PatchCollection
from matplotlib.colors import ListedColormap

# Load the data
try:
    data = pd.read_csv("updated_all_upstream_master_F_July_19.csv")
except FileNotFoundError:
    print("Error: 'updated_all_upstream_master_F_July_19.csv' not found. Please ensure the file is in the correct directory.")
    exit()

# Define mutations of interest
pfcrt_mutations = ['N326S', 'K76T', 'I356T', 'A220S', 'N75E', 'M74I', 'R371I', 'Q271E']
pfmdr1_mutations = ['N86Y', 'Y184F']
pfk13_mutations = ['R622I', 'A675V', 'L143V', 'P441L', 'V714D', 'K189T', 'L258M', 'R255K', 'K189N', 'E433D',
                   'K108E', 'I352T', 'E401Q', 'G26S', 'D281V', 'D211G']

# Filter for missense variants and WHO_reported_SNP
missense_mutations = data[
    (data['Annotation'] == 'missense_variant') &
    (data['SNP_REPORT'] == 'WHO_reported_SNP') &
    ((data['Gene'] == 'Pfcrt') & (data['Mutation'].isin(pfcrt_mutations)) |
     (data['Gene'] == 'Pfmdr1') & (data['Mutation'].isin(pfmdr1_mutations)) |
     (data['Gene'] == 'Pfk13') & (data['Mutation'].isin(pfk13_mutations)))
].copy()

# Get a sorted list of all unique districts for consistent column ordering in the output
all_districts = sorted(missense_mutations['District'].unique())

# Create a mapping from Sample_ID to District for efficient lookup
sample_to_district = missense_mutations.drop_duplicates(subset='Sample_ID').set_index('Sample_ID')['District'].to_dict()


# Function to generate co-occurring mutation pairs and track their districts
def generate_co_occurring_pairs_with_districts(mutations, sample_district_map):
    """
    Generates co-occurring mutation pairs and stores a list of districts for each occurrence.
    """
    co_occurring_pairs = {}
    for sample_id in mutations['Sample_ID'].unique():
        sample_mutations = mutations[mutations['Sample_ID'] == sample_id]
        district = sample_district_map.get(sample_id)
        # Ensure we have a district and at least two mutations to form a pair
        if district and len(sample_mutations) >= 2:
            for (gene1, mut1), (gene2, mut2) in combinations(zip(sample_mutations['Gene'], sample_mutations['Mutation']), 2):
                # Ensure a consistent order for the pair key to avoid duplicate counting
                pair = tuple(sorted(((gene1, mut1), (gene2, mut2))))
                if pair not in co_occurring_pairs:
                    co_occurring_pairs[pair] = []
                co_occurring_pairs[pair].append(district)
    return co_occurring_pairs

# Generate co-occurring pairs with district information
print("Generating co-occurring pairs with district-level tracking...")
co_occurring_pairs_with_districts = generate_co_occurring_pairs_with_districts(missense_mutations, sample_to_district)


# Analyze and store co-occurring pairs, now including district counts
def analyze_co_occurring_pairs(pairs_with_districts, mutations, all_districts_list):
    """
    Performs statistical analysis and counts co-occurrences per district.
    """
    results = []
    total_samples = len(mutations['Sample_ID'].unique())

    for pair, district_list in pairs_with_districts.items():
        # The total observed count is the length of the district list
        count = len(district_list)

        gene1, mut1 = pair[0]
        gene2, mut2 = pair[1]

        # Statistical analysis using contingency table
        samples_with_mut1 = set(mutations[(mutations['Gene'] == gene1) & (mutations['Mutation'] == mut1)]['Sample_ID'])
        samples_with_mut2 = set(mutations[(mutations['Gene'] == gene2) & (mutations['Mutation'] == mut2)]['Sample_ID'])
        a = len(samples_with_mut1 & samples_with_mut2)
        b = len(samples_with_mut1 - samples_with_mut2)
        c = len(samples_with_mut2 - samples_with_mut1)
        d = total_samples - (a + b + c)
        contingency_table = np.array([[a, b], [c, d]])

        if np.all(contingency_table):
            stat, p, dof, expected = chi2_contingency(contingency_table)
        else:
            stat, p = 0, 1

        # Start building the result dictionary for the current pair
        result_row = {
            'Gene1': gene1,
            'Mutation1': mut1,
            'Gene2': gene2,
            'Mutation2': mut2,
            'Observed Count (Total)': count,
            'Same Gene': gene1 == gene2,
            'Chi-squared statistic': stat,
            'P-value': p,
            'Significance': 'Significant' if p < 0.05 else 'Not Significant'
        }

        # Add a column for each district's co-occurrence count
        district_counts = Counter(district_list)
        for district in all_districts_list:
            result_row[district] = district_counts.get(district, 0)

        results.append(result_row)

    return results

# Analyze all co-occurring pairs
print("Analyzing all pairs and their district counts...")
all_results = analyze_co_occurring_pairs(co_occurring_pairs_with_districts, missense_mutations, all_districts)
df_all_results = pd.DataFrame(all_results)

# Format P-value
df_all_results['P-value'] = df_all_results['P-value'].apply(lambda x: f'{x:.4e}' if x < 0.001 else f'{x:.4f}')

# Save all results to Excel
print("Saving complete analysis to Excel...")
df_all_results.to_excel("all_co_occurring_pairs_with_chi2_test_and_significance.xlsx", index=False)
print("File 'all_co_occurring_pairs_with_chi2_test_and_significance.xlsx' created.")

# Analyze top pairs
top_pairs_with_districts = dict(sorted(co_occurring_pairs_with_districts.items(), key=lambda item: len(item[1]), reverse=True)[:250])
results = analyze_co_occurring_pairs(top_pairs_with_districts, missense_mutations, all_districts)
df_results = pd.DataFrame(results)

# Format and save results
df_results['P-value'] = df_results['P-value'].apply(lambda x: f'{x:.4e}' if x < 0.001 else f'{x:.4f}')
print("Saving top 250 pairs analysis to Excel...")
df_results.to_excel("top_250_co_occurring_pairs_with_chi2_test_and_significance.xlsx", index=False)
print("File 'top_250_co_occurring_pairs_with_chi2_test_and_significance.xlsx' created.")


# --- Chord Diagram Visualization ---
print("\nGenerating chord diagram visualization...")
# Create a simple pair:count dictionary for the original visualization function
co_occurring_pairs_simple = {pair: len(districts) for pair, districts in co_occurring_pairs_with_districts.items()}

all_mutations = [(gene, mut) for gene in missense_mutations['Gene'].unique()
                 for mut in missense_mutations[missense_mutations['Gene'] == gene]['Mutation'].unique()]

def draw_chord_diagram(pairs, title, top_n=None):
    if top_n is not None:
        top_pairs_data = dict(sorted(pairs.items(), key=lambda item: item[1], reverse=True)[:top_n])
    else:
        top_pairs_data = pairs
        
    # Filter out connections between variants of the same gene
    top_pairs_data = {pair: count for pair, count in top_pairs_data.items() if pair[0][0] != pair[1][0]}

    graph = nx.Graph()
    for pair, count in top_pairs_data.items():
        node1 = f"{pair[0][0]}\n{pair[0][1]}"
        node2 = f"{pair[1][0]}\n{pair[1][1]}"
        graph.add_edge(node1, node2, weight=count)

    node_counts = {}
    for gene, mut in all_mutations:
        node = f"{gene}\n{mut}"
        if node in graph.nodes:
            node_counts[node] = len(missense_mutations[(missense_mutations['Gene'] == gene) & (missense_mutations['Mutation'] == mut)])
    node_labels = {node: f"{node}\n(n={node_counts.get(node, 0)})" for node in graph.nodes}

    genes = sorted({node.split('\n')[0] for node in graph.nodes})
    gene_colors = {gene: color for gene, color in zip(genes, sns.color_palette("Set1", n_colors=len(genes)))}
    node_colors = [gene_colors[node.split('\n')[0]] for node in graph.nodes]

    edge_colors = [graph[u][v]['weight'] for u, v in graph.edges()]
    norm = plt.Normalize(min(edge_colors), max(edge_colors))
    edge_colors = [plt.cm.viridis(norm(c)) for c in edge_colors]

    pos = nx.circular_layout(graph)

    plt.figure(figsize=(10, 10), dpi=1200)

    nx.draw_networkx_nodes(graph, pos, node_color=node_colors, node_size=3000, edgecolors='black', linewidths=1.2)
    nx.draw_networkx_labels(graph, pos, labels=node_labels, font_size=10, font_weight='bold', font_color='black')
    nx.draw_networkx_edges(graph, pos, edge_color=edge_colors, width=[np.log(w + 1) * 1.5 for w in nx.get_edge_attributes(graph, 'weight').values()], alpha=0.7)

    edge_labels = {(u, v): graph[u][v]['weight'] for u, v in graph.edges()}
    nx.draw_networkx_edge_labels(graph, pos, edge_labels=edge_labels, font_color="darkred", font_size=7, label_pos=0.5, rotate=True, clip_on=False)

    legend_elements = [plt.Line2D([0], [0], marker='o', color='w', label=gene, markersize=12, markerfacecolor=color, markeredgecolor='black', markeredgewidth=0.5) for gene, color in gene_colors.items()]
    legend = plt.legend(handles=legend_elements, title="Gene", loc="upper right", bbox_to_anchor=(1.3, 1), fontsize=10, title_fontsize=12, frameon=True, facecolor='white', edgecolor='black')
    plt.setp(legend.get_title(), color='black')

    plt.title(title, fontsize=18, fontweight='bold')
    plt.axis('off')
    plt.tight_layout(rect=[0, 0, 0.85, 0.96])
    plt.savefig("Co-occurring Mutation Pairs.png", transparent=False, bbox_inches='tight', dpi=1200)
    plt.show()

# Draw the chord diagram for the top 250 pairs
draw_chord_diagram(co_occurring_pairs_simple, "Co-occurring Mutation Pairs", top_n=250)


# --- Heatmap Visualization  ---
print("Generating heatmap visualization...")
heatmap_mutation_list = all_mutations # Reuse the list from the chord diagram section

co_occurrence_matrix = pd.DataFrame(0, index=pd.MultiIndex.from_tuples(heatmap_mutation_list), columns=pd.MultiIndex.from_tuples(heatmap_mutation_list))

for pair, count in co_occurring_pairs_simple.items():
    co_occurrence_matrix.loc[pair[0], pair[1]] = count
    co_occurrence_matrix.loc[pair[1], pair[0]] = count

plt.figure(figsize=(13, 11), dpi=650)
sns.set(font_scale=1.2)
heatmap = sns.heatmap(co_occurrence_matrix, cmap="plasma", annot=False, cbar_kws={'label': 'Co-occurrence Count', 'shrink': 0.7, 'orientation': 'vertical', 'pad': 0.02}, square=True, robust=True, linewidths=0.5, linecolor='gray', fmt='d')

cbar = heatmap.collections[0].colorbar
cbar.ax.tick_params(labelsize=10, color='black')
cbar.outline.set_edgecolor('black')
cbar.outline.set_linewidth(0.8)

plt.title("Co-occurrence Matrix of WHO-reported Missense SNP Mutations", fontsize=20, pad=20, fontweight='bold')
plt.xlabel("Gene, Mutation", fontsize=16, labelpad=15, fontweight='bold')
plt.ylabel("Gene, Mutation", fontsize=16, labelpad=15, fontweight='bold')
plt.xticks(rotation=45, ha='right', fontsize=14, rotation_mode='anchor')
plt.yticks(rotation=0, fontsize=14)

for _, spine in heatmap.spines.items():
    spine.set_visible(True)
    spine.set_linewidth(1.5)
    spine.set_color('black')

plt.tight_layout()
plt.savefig("enhanced_missense_snp_co_occurrence_matrix_heatmap.png", dpi=650, bbox_inches='tight')
plt.show()

print("\nAnalysis and visualization complete.")

Generating co-occurring pairs with district-level tracking...
Analyzing all pairs and their district counts...
Saving complete analysis to Excel...
File 'all_co_occurring_pairs_with_chi2_test_and_significance.xlsx' created.
Saving top 250 pairs analysis to Excel...
File 'top_250_co_occurring_pairs_with_chi2_test_and_significance.xlsx' created.

Generating chord diagram visualization...


Generating heatmap visualization...



Analysis and visualization complete.
